# Reinforcement Learning control strategies for Electric Vehicles fleet Virtual Power Plants
Thesis based on the development of a RL agent that manages a VPP through EVs charging stations in an household environment. Main optimization objectives of the VPP are: Valley filling, peak shaving and zero resulting load over time. Main action performed to reach objectives are: storage of Renewable energy resources and power push in the grid at high demand times. The development of the Virtual Power Plant environment is based on the ELVIS (Electric Vehicles Infrastructure Simulator) open library from DAI-Labor: https://github.com/dailab/elvis The thesis code is currently available at: (https://github.com/francescomaldonato/RL_VPP_Thesis)

Author: Francesco Maldonato

## VPP simulator Notebook based on EVs arrival, with StableBaselines3 trained model (Recurrent PPO) [10 EVs per week test]

Installing required packages and dependencies

In [1]:
%%capture
!pip install py-elvis==0.2.1
!pip install pyyaml==5.4
!pip install plotly==5.9.0
!pip install -U kaleido==0.2.1

!pip install stable-baselines3[extra]==1.6.1
!pip install stable-baselines==1.6.1
!pip install sb3-contrib==1.6.1
!pip install gym==0.20.0
!pip install -q wandb==0.13.4

In [2]:
#Cloning repository and changing directory
!git clone https://github.com/francescomaldonato/RL_VPP_Thesis.git
%cd RL_VPP_Thesis/
%ls

Cloning into 'RL_VPP_Thesis'...
remote: Enumerating objects: 503, done.
remote: Counting objects: 100% (110/110), done.
remote: Compressing objects: 100% (55/55), done.
remote: Total 503 (delta 55), reused 107 (delta 54), pack-reused 393
Receiving objects: 100% (503/503), 184.47 MiB | 22.77 MiB/s, done.
Resolving deltas: 100% (204/204), done.
Checking out files: 100% (226/226), done.
/content/RL_VPP_Thesis
Agent_trainer_notebooks/          log.log          VPP_environment.py
Algorithm_simulator_notebooks/    __pycache__/     VPP_simulator.ipynb
data/                             README.md        wandb/
EV_experiment_notebooks/          RL_VPP_Thesis/
Hyperparameters_sweep_notebooks/  trained_models/


In [3]:
import yaml
import numpy as np
from gym import Env
from VPP_environment import VPPEnv, VPP_Scenario_config
from elvis.config import ScenarioConfig
import os
import torch
import random
import wandb
from sb3_contrib import RecurrentPPO #The available algoritmhs in sb3-contrib for the custom environment with MultiInputPolicy
from sb3_contrib.common.maskable.utils import get_action_masks
import stable_baselines3 as sb3
from stable_baselines3.common.env_checker import check_env

#Check if cuda device is available for training
print("Torch-Cuda available device:", torch.cuda.is_available())
print(sb3.get_system_info())
#!wandb --version

Torch-Cuda available device: False
OS: Linux-5.10.133+-x86_64-with-Ubuntu-18.04-bionic #1 SMP Fri Aug 26 08:44:51 UTC 2022
Python: 3.7.14
Stable-Baselines3: 1.6.1
PyTorch: 1.12.1+cu113
GPU Enabled: False
Numpy: 1.21.6
Gym: 0.20.0

({'OS': 'Linux-5.10.133+-x86_64-with-Ubuntu-18.04-bionic #1 SMP Fri Aug 26 08:44:51 UTC 2022', 'Python': '3.7.14', 'Stable-Baselines3': '1.6.1', 'PyTorch': '1.12.1+cu113', 'GPU Enabled': 'False', 'Numpy': '1.21.6', 'Gym': '0.20.0'}, 'OS: Linux-5.10.133+-x86_64-with-Ubuntu-18.04-bionic #1 SMP Fri Aug 26 08:44:51 UTC 2022\nPython: 3.7.14\nStable-Baselines3: 1.6.1\nPyTorch: 1.12.1+cu113\nGPU Enabled: False\nNumpy: 1.21.6\nGym: 0.20.0\n')


In [4]:
# Ensure deterministic behavior
torch.backends.cudnn.deterministic = True
random.seed(0)
torch.manual_seed(0)
torch.cuda.manual_seed_all(0)

## Load ELVIS YAML config file
Section where the EVs arrival simulation parameters are loaded through the Yaml config file from the 'data/config_builder/' folder.

In [5]:
#Loading paths for input data
current_folder = ''
VPP_training_data_input_path = current_folder + 'data/data_training/environment_table/' + 'Environment_data_2019.csv'
VPP_testing_data_input_path = current_folder + 'data/data_testing/environment_table/' + 'Environment_data_2020.csv'
VPP_validating_data_input_path = current_folder + 'data/data_validating/environment_table/' + 'Environment_data_2018.csv'
elvis_input_folder = current_folder + 'data/config_builder/'

#case = 'wohnblock_household_simulation_adaptive.yaml' #(loaded by default, 20 EVs arrivals per week with 50% average battery)

#Try different simulation parameters, uncomment below
case = 'wohnblock_household_simulation_adaptive_10.yaml' #(10 EVs arrivals per week with 50% average battery) 
#case = 'wohnblock_household_simulation_adaptive_15.yaml' #(15 EVs arrivals per week with 50% average battery)
#case = 'wohnblock_household_simulation_adaptive_25.yaml' #(25 EVs arrivals per week with 50% average battery) 
#case = 'wohnblock_household_simulation_adaptive_30.yaml' #(30 EVs arrivals per week with 50% average battery) 
#case = 'wohnblock_household_simulation_adaptive_35.yaml' #(35 EVs arrivals per week with 50% average battery) 

with open(elvis_input_folder + case, 'r') as file:
    yaml_str = yaml.full_load(file)

elvis_config_file = ScenarioConfig.from_yaml(yaml_str)
VPP_config_file = VPP_Scenario_config(yaml_str)

print(elvis_config_file)
print(VPP_config_file)

Vehicle types: <generator object ScenarioConfig.__str__.<locals>.<genexpr> at 0x7f4e2bb1f7d0>Mean parking time: 23.99
Std deviation of parking time: 1
Mean value of the SOC distribution: 0.5
Std deviation of the SOC distribution: 0.1
Max parking time: 24
Number of charging events per week: 10
Vehicles are disconnected only depending on their parking time
Queue length: 0
Opening hours: None
Scheduling policy: Uncontrolled

{'start_date': '2022-01-01T00:00:00', 'end_date': '2023-01-01T00:00:00', 'resolution': '0:15:00', 'num_households': 4, 'solar_power': 16, 'wind_power': 12, 'EV_types': [{'battery': {'capacity': 100, 'efficiency': 1, 'max_charge_power': 150, 'min_charge_power': 0}, 'brand': 'Tesla', 'model': 'Model S', 'probability': 1}], 'charging_stations_n': 4, 'EVs_n': 10, 'EVs_n_max': 522, 'mean_park': 23.99, 'std_deviation_park': 1, 'EVs_mean_soc': 50.0, 'EVs_std_deviation_soc': 10.0, 'EV_load_max': 44, 'EV_load_rated': 14.8, 'EV_load_min': 1, 'houseRWload_max': 10, 'av_max_energ

In [6]:
#TESTING Environment initialization
env = VPPEnv(VPP_testing_data_input_path, elvis_config_file, VPP_config_file)
env.plot_VPP_input_data()

Output hidden; open in https://colab.research.google.com to view.

In [7]:
env.plot_ELVIS_data()

In [8]:
#Function to check custom environment and output additional warnings if needed
check_env(env)
env.plot_reward_functions()

- ELVIS.Simulation (Av.EV_SOC=  50.0 %):
 Sum_Energy=kWh  3906.06 , over-consume=kWh  24469.68 , under-consume=kWh  20563.62 , Total_cost=€  305.31 , overcost=€  894.83 , Av.EV_en_left=kWh  100.0 , Charging_events=  522 
- Exp.VPP_goals: Energy_consumed=kWh 0, Av.load=kW 0, Std.load=kW 0, Total_cost=€ 0 , Av.EV_en_left=kWh  100.12
Simulating VPP....


### VPP Simulation test with random actions [no model loaded]

In [9]:
episodes = 1
for episode in range(1, episodes+1):
    state = env.reset()
    done = False
    score = 0
    while not done:
        action_masks = get_action_masks(env)
        action = env.action_space.sample()
        
        n_state, reward, done, info = env.step(action)
        score+=reward
    print('Episode:{} Score:{}'.format(episode, score))

VPP_table = env.VPP_table
env.plot_VPP_energies()

Output hidden; open in https://colab.research.google.com to view.

In [10]:
env.plot_Elvis_results()

Output hidden; open in https://colab.research.google.com to view.

In [11]:
env.plot_VPP_results()

Output hidden; open in https://colab.research.google.com to view.

In [12]:
env.plot_VPP_supply_demand()

Output hidden; open in https://colab.research.google.com to view.

In [13]:
env.plot_VPP_Elvis_comparison()

In [14]:
env.plot_rewards_results()

Output hidden; open in https://colab.research.google.com to view.

In [15]:
#env.plot_rewards_stats()

In [16]:
env.plot_EVs_kpi()

In [17]:
env.plot_actions_kpi()

In [18]:
env.plot_load_kpi()

In [19]:
env.plot_yearly_load_log()

Output hidden; open in https://colab.research.google.com to view.

In [20]:
## Wandb login to load models
#In Colab, uncomment below:
# %env "WANDB_DISABLE_CODE" True
# %env "WANDB_NOTEBOOK_NAME" "VPP_simulator.ipynb"
# os.environ['WANDB_NOTEBOOK_NAME'] = 'VPP_simulator.ipynb'
#wandb.login(relogin=True)

#In local notebook, uncomment below:
#your_wandb_login_code = 0123456789abcdefghijklmnopqrstwxyzàèìòù0 #example length
#!wandb login {your_wandb_login_code}

In [21]:
#Loading training model, from local directory or from wandb previous trainings
RecurrentPPO_path = "trained_models/RecurrentPPO_models/model_RecurrentPPO_"

#model_id = "s37o8q0n"
model_id = "333ckz0i"
model = RecurrentPPO.load(RecurrentPPO_path + model_id, env=env)

# run_id_restore = "2y2dqvyn"
# model = wandb.restore(f'model_{run_id_restore}.zip', run_path=f"francesco_maldonato/RL_VPP_Thesis/{run_id_restore}")

/usr/local/lib/python3.7/dist-packages/stable_baselines3/common/save_util.py:169: UserWarning:

Could not deserialize object _last_lstm_states. Consider using `custom_objects` argument to replace this object.



Wrapping the env with a `Monitor` wrapper
Wrapping the env in a DummyVecEnv.


## Testing dataset VPP Simulation using the loaded trained model

In [22]:
#TEST Model
episodes = 1
for episode in range(1, episodes+1):
    obs = env.reset()
    done = False
    score = 0
    # cell and hidden state of the LSTM
    lstm_states = None
    num_envs = 1
    # Episode start signals are used to reset the lstm states
    episode_starts = np.ones((num_envs,), dtype=bool)
    while not done:
        #env.render()
        action_masks = get_action_masks(env)
        action, lstm_states = model.predict(obs, state=lstm_states, episode_start=episode_starts, deterministic=True) #Now using our trained model with deterministic prediction [should improve performances]
        env.lstm_state = lstm_states
        obs, reward, done, info = env.step(action)
        episode_starts = done
        score+=reward
    print('Episode:{} Score:{}'.format(episode, score))

#Save the VPP table
VPP_table = env.save_VPP_table(save_path='data/environment_optimized_output/VPP_table.csv')

- ELVIS.Simulation (Av.EV_SOC=  50.0 %):
 Sum_Energy=kWh  4314.2 , over-consume=kWh  25104.55 , under-consume=kWh  20790.36 , Total_cost=€  344.6 , overcost=€  927.71 , Av.EV_en_left=kWh  100.0 , Charging_events=  522 
- Exp.VPP_goals: Energy_consumed=kWh 0, Av.load=kW 0, Std.load=kW 0, Total_cost=€ 0 , Av.EV_en_left=kWh  100.12
Simulating VPP....
- VPP.Simulation results
 LOAD_INFO: Sum_Energy=KWh  -9585.95 , over-consume=KWh  3979.74 , under-consume=KWh  13565.68 , Total_cost=€  -203.33 , Overcost=€  140.81 
 EV_INFO: Av.EV_energy_leaving=kWh  72.24 , Std.EV_energy_leaving=kWh  23.98 , EV_departures =  522 , EV_queue_left =  0
SCORE:  Cumulative_reward= 209178.17 - Step_rewars (load_t= 200682.6, EVs_energy_t= 14142.42)
 - Final_rewards (EVs_energy= 7750.56, Overconsume= -5654.14, Underconsume= -8484.35, Overcost= 741.08)
Episode:1 Score:209178.1653452875


In [23]:
env.plot_VPP_energies()

Output hidden; open in https://colab.research.google.com to view.

In [24]:
VPP_table.head(15000)

0    1          2         3              EVs_id  \
time                                                                     
2022-01-01 00:00:00  0.0  0.0  46.023872  56.80378        [0, 0, 0, 0]   
2022-01-01 00:15:00  0.0  0.0  45.102646  57.05378  [0, 0, 1566, 1565]   
2022-01-01 00:30:00  0.0  0.0  44.364304  57.30378  [0, 0, 1566, 1565]   
2022-01-01 00:45:00  0.0  0.0  43.741745  57.55378  [0, 0, 1566, 1565]   
2022-01-01 01:00:00  0.0  0.0  43.045864  57.80378  [0, 0, 1566, 1565]   
...                  ...  ...        ...       ...                 ...   
2022-06-06 04:45:00  0.0  0.0   0.000000   0.00000        [0, 0, 0, 0]   
2022-06-06 05:00:00  0.0  0.0   0.000000   0.00000        [0, 0, 0, 0]   
2022-06-06 05:15:00  0.0  0.0   0.000000   0.00000        [0, 0, 0, 0]   
2022-06-06 05:30:00  0.0  0.0   0.000000   0.00000        [0, 0, 0, 0]   
2022-06-06 05:45:00  0.0  0.0   0.000000   0.00000        [0, 0, 0, 0]   

                          actions                    mask_truth  \
time                                                              
2022-01-01 00:00:00  [2, 2, 2, 1]  [False, False, False, False]   
2022-01-01 00:15:00  [2, 2, 2, 1]   [False, False, True, False]   
2022-01-01 00:30:00  [2, 2, 2, 1]   [False, False, True, False]   
2022-01-01 00:45:00  [2, 2, 2, 1]   [False, False, True, False]   
2022-01-01 01:00:00  [2, 2, 2, 1]   [False, False, True, False]   
...                           ...                           ...   
2022-06-06 04:45:00  [2, 2, 1, 2]  [False, False, False, False]   
2022-06-06 05:00:00  [2, 2, 1, 2]  [False, False, False, False]   
2022-06-06 05:15:00  [2, 2, 2, 2]  [False, False, False, False]   
2022-06-06 05:30:00  [2, 2, 2, 2]  [False, False, False, False]   
2022-06-06 05:45:00  [2, 2, 2, 2]  [False, False, False, False]   

                     ev_charged_pwr  ev_discharged_pwr          load  \
time                                                                   
2022-01-01 00:00:00             0.0           0.000000  2.228419e+00   
2022-01-01 00:15:00             1.0          -3.684902  0.000000e+00   
2022-01-01 00:30:00             1.0          -2.953363  2.220446e-16   
2022-01-01 00:45:00             1.0          -2.490237  2.220446e-16   
2022-01-01 01:00:00             1.0          -2.783523  2.220446e-16   
...                             ...                ...           ...   
2022-06-06 04:45:00             0.0           0.000000 -8.168801e+00   
2022-06-06 05:00:00             0.0           0.000000 -1.219049e+01   
2022-06-06 05:15:00             0.0           0.000000 -1.204223e+01   
2022-06-06 05:30:00             0.0           0.000000 -1.202744e+01   
2022-06-06 05:45:00             0.0           0.000000 -1.177434e+01   

                     load_reward  EV_reward    rewards  
time                                                    
2022-01-01 00:00:00    15.000000        0.0  15.000000  
2022-01-01 00:15:00    15.000000        0.0  15.000000  
2022-01-01 00:30:00    15.000000        0.0  15.000000  
2022-01-01 00:45:00    15.000000        0.0  15.000000  
2022-01-01 01:00:00    15.000000        0.0  15.000000  
...                          ...        ...        ...  
2022-06-06 04:45:00   -12.445899        0.0 -12.445899  
2022-06-06 05:00:00   -12.311122        0.0 -12.311122  
2022-06-06 05:15:00   -12.297677        0.0 -12.297677  
2022-06-06 05:30:00   -12.067582        0.0 -12.067582  
2022-06-06 05:45:00   -12.386132        0.0 -12.386132  

[15000 rows x 13 columns]

In [25]:
#env.plot_Elvis_results()

In [26]:
env.plot_VPP_results()

Output hidden; open in https://colab.research.google.com to view.

In [27]:
env.plot_VPP_supply_demand()

Output hidden; open in https://colab.research.google.com to view.

In [28]:
env.plot_VPP_Elvis_comparison()

In [29]:
env.plot_rewards_results()

Output hidden; open in https://colab.research.google.com to view.

In [30]:
env.plot_rewards_stats()

In [31]:
env.plot_EVs_kpi()

In [32]:
env.plot_load_kpi()

In [33]:
env.plot_yearly_load_log()

Output hidden; open in https://colab.research.google.com to view.

## Validating dataset VPP Simulation using the loaded trained model

In [34]:
#VALIDATING Environment initialization
env = VPPEnv(VPP_validating_data_input_path, elvis_config_file, VPP_config_file)

Charging event: 2089, Arrival time: 2022-01-01 14:15:00, Parking_time: 24, Leaving_time: 2022-01-02 14:15:00, SOC: 0.5057686492519093, SOC target: 1.0, Connected car: Tesla, Model S 
 ... 
 Charging event: 2610, Arrival time: 2022-12-31 23:45:00, Parking_time: 24, Leaving_time: 2023-01-01 23:45:00, SOC: 0.4402547690971162, SOC target: 1.0, Connected car: Tesla, Model S 

-DATASET: House&RW_energy_sum=kWh  -30085.39 , over-consume=kWh  2136.67 , under-consume=kWh  -32222.06 , Total_cost=€  -1187.15 , overcost=€  113.34
- ELVIS.Simulation (Av.EV_SOC=  50.0 %):
 Sum_Energy=kWh  -5065.23 , over-consume=kWh  20329.09 , under-consume=kWh  25394.32 , Total_cost=€  -100.88 , overcost=€  913.88 , Charging_events=  522 
- Exp.VPP_goals: Energy_consumed=kWh 0, Av.load=kW 0, Std.load=kW 0, Total_cost=€ 0 , Av.EV_en_left=kWh  111.73


In [35]:
#Function to check custom environment and output additional warnings if needed
check_env(env)
plot_VPP_input_data = env.plot_VPP_input_data()
plot_VPP_input_data.show()

Output hidden; open in https://colab.research.google.com to view.

In [36]:
#model = PPO.load(PPO_path + model_run_ID, env = env)
model = RecurrentPPO.load(RecurrentPPO_path + model_id, env=env)

Wrapping the env with a `Monitor` wrapper
Wrapping the env in a DummyVecEnv.


/usr/local/lib/python3.7/dist-packages/stable_baselines3/common/save_util.py:169: UserWarning:

Could not deserialize object _last_lstm_states. Consider using `custom_objects` argument to replace this object.



In [37]:
#TEST Model
episodes = 1
for episode in range(1, episodes+1):
    obs = env.reset()
    done = False
    score = 0
    # cell and hidden state of the LSTM
    lstm_states = None
    num_envs = 1
    # Episode start signals are used to reset the lstm states
    episode_starts = np.ones((num_envs,), dtype=bool)
    while not done:
        #env.render()
        action_masks = get_action_masks(env)
        action, lstm_states = model.predict(obs, state=lstm_states, episode_start=episode_starts, deterministic=True) #Now using our trained model with deterministic prediction [should improve performances]
        env.lstm_state = lstm_states
        obs, reward, done, info = env.step(action)
        episode_starts = done
        score+=reward
    print('Episode:{} Score:{}'.format(episode, score))

VPP_table = env.VPP_table
#print(env.lstm_states_list)

- ELVIS.Simulation (Av.EV_SOC=  50.0 %):
 Sum_Energy=kWh  -5495.44 , over-consume=kWh  19975.92 , under-consume=kWh  25471.36 , Total_cost=€  -158.27 , overcost=€  878.67 , Av.EV_en_left=kWh  100.0 , Charging_events=  522 
- Exp.VPP_goals: Energy_consumed=kWh 0, Av.load=kW 0, Std.load=kW 0, Total_cost=€ 0 , Av.EV_en_left=kWh  111.73
Simulating VPP....
- VPP.Simulation results
 LOAD_INFO: Sum_Energy=KWh  -15442.31 , over-consume=KWh  2090.78 , under-consume=KWh  17533.1 , Total_cost=€  -605.92 , Overcost=€  93.66 
 EV_INFO: Av.EV_energy_leaving=kWh  78.21 , Std.EV_energy_leaving=kWh  21.42 , EV_departures =  522 , EV_queue_left =  0
SCORE:  Cumulative_reward= 211280.42 - Step_rewars (load_t= 190391.7, EVs_energy_t= 24252.36)
 - Final_rewards (EVs_energy= 8281.52, Overconsume= -3455.72, Underconsume= -9156.48, Overcost= 967.05)
Episode:1 Score:211280.42365650684


In [38]:
env.plot_VPP_energies()

Output hidden; open in https://colab.research.google.com to view.

In [39]:
VPP_table.head(15000)

0    1          2          3  \
time                                                        
2022-01-01 00:00:00   0.000000  0.0   0.000000   0.000000   
2022-01-01 00:15:00  40.773369  0.0   0.000000   0.000000   
2022-01-01 00:30:00  41.807991  0.0   0.000000   0.000000   
2022-01-01 00:45:00  42.611526  0.0   0.000000   0.000000   
2022-01-01 01:00:00  43.692917  0.0   0.000000   0.000000   
...                        ...  ...        ...        ...   
2022-06-06 04:45:00  57.973526  0.0  99.989998  94.545975   
2022-06-06 05:00:00  57.973526  0.0  99.989998  96.368080   
2022-06-06 05:15:00  57.973526  0.0  99.989998  98.219986   
2022-06-06 05:30:00  57.973526  0.0  99.989998  99.907684   
2022-06-06 05:45:00  57.973526  0.0  99.989998  99.989998   

                                    EVs_id       actions  \
time                                                       
2022-01-01 00:00:00           [0, 0, 0, 0]  [2, 1, 1, 0]   
2022-01-01 00:15:00        [3133, 0, 0, 0]  [1, 0, 0, 0]   
2022-01-01 00:30:00        [3133, 0, 0, 0]  [1, 0, 0, 0]   
2022-01-01 00:45:00        [3133, 0, 0, 0]  [1, 0, 0, 0]   
2022-01-01 01:00:00        [3133, 0, 0, 0]  [1, 0, 0, 0]   
...                                    ...           ...   
2022-06-06 04:45:00  [3361, 0, 3362, 3360]  [0, 2, 1, 1]   
2022-06-06 05:00:00  [3361, 0, 3362, 3360]  [0, 2, 1, 1]   
2022-06-06 05:15:00  [3361, 0, 3362, 3360]  [0, 2, 1, 1]   
2022-06-06 05:30:00  [3361, 0, 3362, 3360]  [0, 2, 1, 1]   
2022-06-06 05:45:00  [3361, 0, 3362, 3360]  [0, 2, 1, 1]   

                                       mask_truth  ev_charged_pwr  \
time                                                                
2022-01-01 00:00:00   [False, False, False, True]        0.000000   
2022-01-01 00:15:00      [True, True, True, True]        0.000000   
2022-01-01 00:30:00      [True, True, True, True]        4.138487   
2022-01-01 00:45:00      [True, True, True, True]        3.214138   
2022-01-01 01:00:00      [True, True, True, True]        4.325562   
...                                           ...             ...   
2022-06-06 04:45:00  [False, False, False, False]        5.160762   
2022-06-06 05:00:00  [False, False, False, False]        7.288428   
2022-06-06 05:15:00  [False, False, False, False]        7.407640   
2022-06-06 05:30:00  [False, False, False, False]        6.750792   
2022-06-06 05:45:00  [False, False, False, False]        0.329271   

                     ev_discharged_pwr       load  load_reward  EV_reward  \
time                                                                        
2022-01-01 00:00:00                0.0  -2.553005    -4.021889        0.0   
2022-01-01 00:15:00                0.0  -3.413133    15.000000        0.0   
2022-01-01 00:30:00                0.0   0.000000    15.000000        0.0   
2022-01-01 00:45:00                0.0   0.000000    15.000000        0.0   
2022-01-01 01:00:00                0.0   0.000000    15.000000        0.0   
...                                ...        ...          ...        ...   
2022-06-06 04:45:00                0.0  -5.160745    -7.989464        0.0   
2022-06-06 05:00:00                0.0  -7.288411    -8.097839        0.0   
2022-06-06 05:15:00                0.0  -7.407622    -7.500705        0.0   
2022-06-06 05:30:00                0.0  -6.750775   -14.223199        0.0   
2022-06-06 05:45:00                0.0 -14.145519   -16.559476        0.0   

                       rewards  
time                            
2022-01-01 00:00:00  -4.021889  
2022-01-01 00:15:00  15.000000  
2022-01-01 00:30:00  15.000000  
2022-01-01 00:45:00  15.000000  
2022-01-01 01:00:00  15.000000  
...                        ...  
2022-06-06 04:45:00  -7.989464  
2022-06-06 05:00:00  -8.097839  
2022-06-06 05:15:00  -7.500705  
2022-06-06 05:30:00 -14.223199  
2022-06-06 05:45:00 -16.559476  

[15000 rows x 13 columns]

In [40]:
env.plot_VPP_results()


Output hidden; open in https://colab.research.google.com to view.

In [41]:
env.plot_VPP_supply_demand()

Output hidden; open in https://colab.research.google.com to view.

In [42]:
env.plot_VPP_Elvis_comparison()

In [43]:
env.plot_rewards_results()

Output hidden; open in https://colab.research.google.com to view.

In [44]:
env.plot_rewards_stats()

In [45]:
env.plot_EVs_kpi()

In [46]:
env.plot_load_kpi()

In [47]:
env.plot_yearly_load_log()

Output hidden; open in https://colab.research.google.com to view.

## Training dataset VPP Simulation using the loaded trained model

In [48]:
#TRAINING Environment initialization
env = VPPEnv(VPP_training_data_input_path, elvis_config_file, VPP_config_file)

Charging event: 3655, Arrival time: 2022-01-01 08:30:00, Parking_time: 24, Leaving_time: 2022-01-02 08:30:00, SOC: 0.4573582295135911, SOC target: 1.0, Connected car: Tesla, Model S 
 ... 
 Charging event: 4176, Arrival time: 2022-12-31 07:15:00, Parking_time: 24, Leaving_time: 2023-01-01 07:15:00, SOC: 0.4091012238789611, SOC target: 1.0, Connected car: Tesla, Model S 

-DATASET: House&RW_energy_sum=kWh  -34117.7 , over-consume=kWh  1556.25 , under-consume=kWh  -35673.95 , Total_cost=€  -1196.64 , overcost=€  97.86
- ELVIS.Simulation (Av.EV_SOC=  50.0 %):
 Sum_Energy=kWh  -9102.79 , over-consume=kWh  18189.23 , under-consume=kWh  27292.02 , Total_cost=€  -232.02 , overcost=€  770.27 , Charging_events=  522 
- Exp.VPP_goals: Energy_consumed=kWh 0, Av.load=kW 0, Std.load=kW 0, Total_cost=€ 0 , Av.EV_en_left=kWh  118.34


In [49]:
#Function to check custom environment and output additional warnings if needed
check_env(env)
plot_VPP_input_data = env.plot_VPP_input_data()
plot_VPP_input_data.show()

Output hidden; open in https://colab.research.google.com to view.

In [50]:
#model = PPO.load(PPO_path + model_run_ID, env = env)
model = RecurrentPPO.load(RecurrentPPO_path + model_id, env=env)

Wrapping the env with a `Monitor` wrapper
Wrapping the env in a DummyVecEnv.


/usr/local/lib/python3.7/dist-packages/stable_baselines3/common/save_util.py:169: UserWarning:

Could not deserialize object _last_lstm_states. Consider using `custom_objects` argument to replace this object.



In [51]:
#TEST Model
episodes = 1
for episode in range(1, episodes+1):
    obs = env.reset()
    done = False
    score = 0
    # cell and hidden state of the LSTM
    lstm_states = None
    num_envs = 1
    # Episode start signals are used to reset the lstm states
    episode_starts = np.ones((num_envs,), dtype=bool)
    while not done:
        #env.render()
        action_masks = get_action_masks(env)
        action, lstm_states = model.predict(obs, state=lstm_states, episode_start=episode_starts, deterministic=True) #Now using our trained model with deterministic prediction [should improve performances]
        env.lstm_state = lstm_states
        obs, reward, done, info = env.step(action)
        episode_starts = done
        score+=reward
    print('Episode:{} Score:{}'.format(episode, score))

VPP_table = env.VPP_table
#print(env.lstm_states_list)

- ELVIS.Simulation (Av.EV_SOC=  50.0 %):
 Sum_Energy=kWh  -9265.26 , over-consume=kWh  19015.33 , under-consume=kWh  28280.59 , Total_cost=€  -202.61 , overcost=€  821.56 , Av.EV_en_left=kWh  100.0 , Charging_events=  522 
- Exp.VPP_goals: Energy_consumed=kWh 0, Av.load=kW 0, Std.load=kW 0, Total_cost=€ 0 , Av.EV_en_left=kWh  118.34
Simulating VPP....
- VPP.Simulation results
 LOAD_INFO: Sum_Energy=KWh  -18352.06 , over-consume=KWh  1684.41 , under-consume=KWh  20036.47 , Total_cost=€  -625.06 , Overcost=€  70.5 
 EV_INFO: Av.EV_energy_leaving=kWh  80.52 , Std.EV_energy_leaving=kWh  20.02 , EV_departures =  520 , EV_queue_left =  0
SCORE:  Cumulative_reward= 198641.47 - Step_rewars (load_t= 172204.55, EVs_energy_t= 27212.6)
 - Final_rewards (EVs_energy= 7861.27, Overconsume= -2799.26, Underconsume= -9534.16, Overcost= 3696.46)
Episode:1 Score:198641.46844496008


In [52]:
env.plot_VPP_energies()

Output hidden; open in https://colab.research.google.com to view.

In [53]:
VPP_table.head(14995)

0    1    2    3           EVs_id       actions  \
time                                                                           
2022-01-01 00:00:00   0.000000  0.0  0.0  0.0     [0, 0, 0, 0]  [2, 1, 1, 0]   
2022-01-01 00:15:00   0.000000  0.0  0.0  0.0     [0, 0, 0, 0]  [2, 1, 1, 0]   
2022-01-01 00:30:00   0.000000  0.0  0.0  0.0     [0, 0, 0, 0]  [2, 1, 1, 0]   
2022-01-01 00:45:00   0.000000  0.0  0.0  0.0     [0, 0, 0, 0]  [2, 1, 1, 0]   
2022-01-01 01:00:00   0.000000  0.0  0.0  0.0     [0, 0, 0, 0]  [2, 0, 1, 0]   
...                        ...  ...  ...  ...              ...           ...   
2022-06-06 03:30:00  93.258759  0.0  0.0  0.0  [4907, 0, 0, 0]  [2, 2, 0, 0]   
2022-06-06 03:45:00  92.333755  0.0  0.0  0.0  [4907, 0, 0, 0]  [1, 0, 0, 0]   
2022-06-06 04:00:00  93.993919  0.0  0.0  0.0  [4907, 0, 0, 0]  [1, 0, 0, 0]   
2022-06-06 04:15:00  95.774872  0.0  0.0  0.0  [4907, 0, 0, 0]  [1, 0, 0, 0]   
2022-06-06 04:30:00  97.385704  0.0  0.0  0.0  [4907, 0, 0, 0]  [1, 0, 0, 0]   

                                      mask_truth  ev_charged_pwr  \
time                                                               
2022-01-01 00:00:00  [False, False, False, True]        0.000000   
2022-01-01 00:15:00  [False, False, False, True]        0.000000   
2022-01-01 00:30:00  [False, False, False, True]        0.000000   
2022-01-01 00:45:00  [False, False, False, True]        0.000000   
2022-01-01 01:00:00   [False, True, False, True]        0.000000   
...                                          ...             ...   
2022-06-06 03:30:00   [False, False, True, True]        3.338214   
2022-06-06 03:45:00     [True, True, True, True]        0.000000   
2022-06-06 04:00:00     [True, True, True, True]        6.640649   
2022-06-06 04:15:00     [True, True, True, True]        7.123820   
2022-06-06 04:30:00     [True, True, True, True]        6.443331   

                     ev_discharged_pwr      load  load_reward  EV_reward  \
time                                                                       
2022-01-01 00:00:00                0.0 -3.961052    -4.502729        0.0   
2022-01-01 00:15:00                0.0 -3.701637    -4.246147        0.0   
2022-01-01 00:30:00                0.0 -3.547688    -3.168660        0.0   
2022-01-01 00:45:00                0.0 -2.901196    -6.519861        0.0   
2022-01-01 01:00:00                0.0 -5.671847    -6.419688        0.0   
...                                ...       ...          ...        ...   
2022-06-06 03:30:00                0.0  0.000000    -8.711804        0.0   
2022-06-06 03:45:00               -3.7 -8.082984    15.000000        0.0   
2022-06-06 04:00:00                0.0  0.000000    15.000000        0.0   
2022-06-06 04:15:00                0.0  0.000000    15.000000        0.0   
2022-06-06 04:30:00                0.0  0.000000    15.000000        0.0   

                       rewards  
time                            
2022-01-01 00:00:00  -4.502729  
2022-01-01 00:15:00  -4.246147  
2022-01-01 00:30:00  -3.168660  
2022-01-01 00:45:00  -6.519861  
2022-01-01 01:00:00  -6.419688  
...                        ...  
2022-06-06 03:30:00  -8.711804  
2022-06-06 03:45:00  15.000000  
2022-06-06 04:00:00  15.000000  
2022-06-06 04:15:00  15.000000  
2022-06-06 04:30:00  15.000000  

[14995 rows x 13 columns]

In [54]:
env.plot_VPP_results()

Output hidden; open in https://colab.research.google.com to view.

In [55]:
env.plot_VPP_supply_demand()

Output hidden; open in https://colab.research.google.com to view.

In [56]:
env.plot_VPP_Elvis_comparison()

In [57]:
env.plot_rewards_results()

Output hidden; open in https://colab.research.google.com to view.

In [58]:
env.plot_rewards_stats()

In [59]:
env.plot_EVs_kpi()

In [60]:
env.plot_actions_kpi()

In [61]:
env.plot_load_kpi()

In [62]:
env.plot_yearly_load_log()

Output hidden; open in https://colab.research.google.com to view.

In [63]:
#env.close()